In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [3]:
import os 
import numpy as np 
import sklearn as sk 
import matplotlib.pyplot as plt
import pandas as pd 

In [5]:
try:
    train_df = pd.read_csv('train_fraud.csv')
    # test_df = pd.read_csv('/kaggle/input/fraud-detection/fraudTest.csv')
except:
    train_df = pd.read_csv('train_fraud.csv')
    # test_df = pd.read_csv('fraudTest.csv')
train_df.head()




trans_date_trans_time        cc_num                        merchant  \
0      20-03-2019 15:58  4.067140e+15               fraud_Reichel LLC   
1      01-12-2019 17:38  4.302480e+15                 fraud_Terry Ltd   
2      28-03-2019 13:14  2.576710e+15                 fraud_Thiel Ltd   
3      20-08-2019 16:13  4.358140e+18           fraud_Kirlin and Sons   
4      26-09-2019 15:56  4.561550e+12  fraud_Kihn, Brakus and Goyette   

        category    amt      first       last gender  \
0  personal_care   2.65  Christina      Eaton      F   
1           home  60.29      David  Rodriguez      M   
2         travel   4.63     Joseph     Morgan      M   
3  personal_care  46.96       Dawn   Stephens      F   
4  personal_care   8.03     Daniel     Briggs      M   

                          street       city  ...      lat      long  city_pop  \
0              3256 Brooks Field   Eldridge  ...  33.9315  -87.6194      1186   
1               821 Solis Points   Muskegon  ...  43.2326  -86.2492    128715   
2            126 Underwood Drive  San Diego  ...  33.0067 -117.0690   1241364   
3  91542 Marissa Shores Apt. 053       Oran  ...  42.7012  -92.0762        53   
4   7118 Jessica Unions Apt. 789   Moriarty  ...  34.9889 -106.0609      7268   

                                                 job         dob  \
0                             Politician's assistant  12-11-1986   
1  Historic buildings inspector/conservation officer  25-05-1995   
2                Chartered public finance accountant  05-08-1959   
3                               Sports administrator  05-10-1972   
4                                     Therapist, art  04-08-1988   

                          trans_num   unix_time  merch_lat  merch_long  \
0  b81274f1a07a81d336c6a91a296c6730  1332259099  34.102692  -87.253668   
1  9bf3fc929f2ebe12a09b66814634bbd7  1354383517  43.015449  -86.997300   
2  485843aa45a4ae467b33456270bbba6b  1332940445  32.473763 -117.926979   
3  72ae0c2023761bcfa41b86909cfcab8d  1345479202  43.206432  -92.968102   
4  85aec23fb5b970a736e98f969d2622e6  1348674968  35.697609 -105.756602   

   is_fraud  
0         0  
1         0  
2         0  
3         0  
4         0  

[5 rows x 22 columns]

In [3]:
# train_fraud=train_df.sample(n=100000)

# train_fraud.to_csv("train_fraud.csv",index=False)

In [6]:
train_df.isnull().sum()

trans_date_trans_time    0
cc_num                   0
merchant                 0
category                 0
amt                      0
first                    0
last                     0
gender                   0
street                   0
city                     0
state                    0
zip                      0
lat                      0
long                     0
city_pop                 0
job                      0
dob                      0
trans_num                0
unix_time                0
merch_lat                0
merch_long               0
is_fraud                 0
dtype: int64

In [5]:
# def data_pre(X):
#     del_col=['merchant','first','last','street','zip','unix_time','trans_num','cc_num','city_pop']
#     X.drop(columns=del_col,inplace=True)
   
    
#     X['trans_date_trans_time']=pd.to_datetime(X['trans_date_trans_time'])
#     X['trans_date']=X['trans_date_trans_time'].dt.strftime('%d-%m-%Y')
#     X['trans_date']=pd.to_datetime(X['trans_date'])
    
    
#     X['dob']=pd.to_datetime(X['dob'])
    
#     #Calculate Age of each trans 
#     X["age"] = (X["trans_date"] - X["dob"]).dt.days //365

    
#     X['trans_month']=X['trans_date'].dt.month
#     X['trans_year']=X['trans_date'].dt.year
    
#     X['gender']=X['gender'].apply(lambda x : 1 if x=='M' else 0)
#     X['gender']=X['gender'].astype(int)
#     X['lat_dis']=abs(X['lat']-X['merch_lat'])
#     X['long_dis']=abs(X['long']-X['merch_long'])
# #     X=pd.get_dummies(X,columns=['category'])
#     X=X.drop(columns=['city','trans_date_trans_time','state','job','merch_lat','merch_long','lat','long','dob','trans_date'])
#     return X
    

In [6]:
# train_df_pre=data_pre(train_df.copy())
# train_df_pre.head()
# train_df_pre=train_df_pre.sample(n=100000)
# # sample_df = train_df_pre.sample(n=100000)
# # sample_df.to_csv('train.csv',index=False)

In [7]:
import pandas as pd

def data_pre(X):
    del_col=['merchant','first','last','street','zip','unix_time','trans_num','cc_num','city_pop']
    X.drop(columns=del_col, inplace=True)
    
    X['trans_date_trans_time'] = pd.to_datetime(X['trans_date_trans_time'], errors='coerce')
    X['dob'] = pd.to_datetime(X['dob'], errors='coerce')
    
    X['trans_date'] = pd.to_datetime(X['trans_date_trans_time'], errors='coerce', format='%d-%m-%Y', dayfirst=True)
    X['dob'] = pd.to_datetime(X['dob'], errors='coerce', format='%d-%m-%Y', dayfirst=True)
    
    X["age"] = (X["trans_date"] - X["dob"]).dt.days // 365
    
    X['trans_month'] = X['trans_date'].dt.month
    X['trans_year'] = X['trans_date'].dt.year
    
    X['gender'] = X['gender'].apply(lambda x: 1 if x == 'M' else 0).astype(int)
    X['lat_dis'] = abs(X['lat'] - X['merch_lat'])
    X['long_dis'] = abs(X['long'] - X['merch_long'])
    
    X = X.drop(columns=['city', 'trans_date_trans_time', 'state', 'job', 'merch_lat', 'merch_long', 'lat', 'long', 'dob', 'trans_date'])
    return X

train_df_pre = data_pre(train_df.copy().sample(n=100000))
train_df_pre.head()


category    amt  gender  is_fraud   age  trans_month  trans_year  \
81998       misc_net  82.60       1         0  40.0         12.0      2019.0   
28929  gas_transport  59.23       0         0   NaN          NaN         NaN   
12407   shopping_pos   2.95       0         0   NaN         10.0      2020.0   
1756    shopping_pos   6.74       0         0   NaN          NaN         NaN   
95736         travel   6.86       0         0   NaN          NaN         NaN   

        lat_dis  long_dis  
81998  0.249721  0.291817  
28929  0.519176  0.146462  
12407  0.520650  0.338007  
1756   0.528571  0.465378  
95736  0.108462  0.378325

In [8]:
train_df_pre

category     amt  gender  is_fraud   age  trans_month  trans_year  \
81998       misc_net   82.60       1         0  40.0         12.0      2019.0   
28929  gas_transport   59.23       0         0   NaN          NaN         NaN   
12407   shopping_pos    2.95       0         0   NaN         10.0      2020.0   
1756    shopping_pos    6.74       0         0   NaN          NaN         NaN   
95736         travel    6.86       0         0   NaN          NaN         NaN   
...              ...     ...     ...       ...   ...          ...         ...   
54877   shopping_net   10.86       0         0  15.0          4.0      2020.0   
13477  personal_care  166.39       0         0   NaN          3.0      2019.0   
3866            home   42.10       0         0   NaN          NaN         NaN   
8087    shopping_pos    7.90       0         0   NaN          NaN         NaN   
98851  personal_care   32.69       0         0   NaN          NaN         NaN   

        lat_dis  long_dis  
81998  0.249721  0.291817  
28929  0.519176  0.146462  
12407  0.520650  0.338007  
1756   0.528571  0.465378  
95736  0.108462  0.378325  
...         ...       ...  
54877  0.181242  0.363662  
13477  0.653315  0.303410  
3866   0.925161  0.415295  
8087   0.539443  0.730454  
98851  0.738310  0.502839  

[100000 rows x 9 columns]

In [9]:
train_df_pre['is_fraud'].value_counts()

is_fraud
0    99412
1      588
Name: count, dtype: int64

In [15]:
train_df_pre['category'].value_counts()

category
gas_transport     10119
home               9564
grocery_pos        9533
shopping_pos       9103
kids_pets          8643
shopping_net       7529
entertainment      7196
food_dining        7098
personal_care      6993
health_fitness     6721
misc_pos           6084
misc_net           4893
grocery_net        3413
travel             3111
Name: count, dtype: int64

In [16]:
train_df_pre['category'].value_counts()

# """""""gas_transport     2
#grocery_pos        4
#home               6
# shopping_pos       12
# kids_pets          7
# shopping_net       11
# entertainment      0
# food_dining        1
# personal_care      10
# health_fitness     5
# misc_pos           9
# misc_net           8
# grocery_net        3
# travel           13"""""""

category
gas_transport     10119
home               9564
grocery_pos        9533
shopping_pos       9103
kids_pets          8643
shopping_net       7529
entertainment      7196
food_dining        7098
personal_care      6993
health_fitness     6721
misc_pos           6084
misc_net           4893
grocery_net        3413
travel             3111
Name: count, dtype: int64

In [17]:
from sklearn.preprocessing import LabelEncoder

# Assuming 'test_df_pre' is your DataFrame and 'category' is the column you want to encode
label_encoder = LabelEncoder()
train_df_pre['category'] = label_encoder.fit_transform(train_df_pre['category'])


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):


In [18]:
train_df_pre['category'].value_counts()

category
2     10119
6      9564
4      9533
12     9103
7      8643
11     7529
0      7196
1      7098
10     6993
5      6721
9      6084
8      4893
3      3413
13     3111
Name: count, dtype: int64

In [19]:
train_df_pre['is_fraud'].value_counts()

is_fraud
0    99412
1      588
Name: count, dtype: int64

In [20]:
train_df_pre.columns

Index(['category', 'amt', 'gender', 'is_fraud', 'age', 'trans_month',
       'trans_year', 'lat_dis', 'long_dis'],
      dtype='object')

In [21]:
train_df_pre['trans_year'].value_counts()

trans_year
2019    71229
2020    28771
Name: count, dtype: int64

In [22]:
train_df_pre.describe()

category            amt         gender       is_fraud  \
count  100000.000000  100000.000000  100000.000000  100000.000000   
mean        6.235250      71.589179       0.451570       0.005880   
std         3.913684     173.993328       0.497651       0.076456   
min         0.000000       1.000000       0.000000       0.000000   
25%         3.000000       9.650000       0.000000       0.000000   
50%         6.000000      47.840000       0.000000       0.000000   
75%        10.000000      84.000000       1.000000       0.000000   
max        13.000000   14467.640000       1.000000       1.000000   

                 age    trans_month     trans_year        lat_dis  \
count  100000.000000  100000.000000  100000.000000  100000.000000   
mean       45.604250       6.151320    2019.287710       0.498702   
std        17.464104       3.416404       0.452697       0.288948   
min        13.000000       1.000000    2019.000000       0.000012   
25%        32.000000       3.000000    2019.000000       0.247623   
50%        44.000000       6.000000    2019.000000       0.496935   
75%        57.000000       9.000000    2020.000000       0.749578   
max        95.000000      12.000000    2020.000000       0.999997   

            long_dis  
count  100000.000000  
mean        0.500467  
std         0.288491  
min         0.000014  
25%         0.249969  
50%         0.500003  
75%         0.749878  
max         0.999995

In [23]:
# train_df_pre.to_csv("fraud_clean.csv",index=False)

In [24]:
x=train_df_pre.drop('is_fraud',axis=1)
y=train_df_pre['is_fraud']

In [25]:
from imblearn.over_sampling import RandomOverSampler
rs=RandomOverSampler(random_state=42)
X,Y= rs.fit_resample(x,y)

Y.value_counts()

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed 

is_fraud
0    99412
1    99412
Name: count, dtype: int64

In [26]:
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test = train_test_split(X,Y,test_size = 0.2,random_state =42)

In [27]:
# from sklearn.preprocessing import StandardScaler

# # Step 1: Fit the StandardScaler on the training data
# scaler = StandardScaler()
# scaler.fit(x_train)
# x_train=scaler.transform(x_train)
# x_test=scaler.transform(x_test)

In [28]:
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, classification_report

In [29]:

# logistic regression

LR = LogisticRegression()
LR.fit(x_train, y_train)


# prediction
train_prediction= LR.predict(x_train)
test_prediction= LR.predict(x_test)
print('*'*20)

# evaluation
from sklearn.metrics import accuracy_score
print('test accuracy:',accuracy_score(y_test,test_prediction))
print('train accuracy:',accuracy_score(y_train,train_prediction))
print('*'*20)

# cross validation score
from sklearn.model_selection import cross_val_score
score=cross_val_score(LR,X,Y,cv=5)
print(score.mean())
print('*'*20)

print(classification_report(y_test,test_prediction))

print('*'*20)


lr_HSC = accuracy_score(y_test,test_prediction)
print(f"{round(lr_HSC*100,2)}% Accurate")

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarn

********************
test accuracy: 0.8570853765874513
train accuracy: 0.8556699086502493
********************


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarn

0.855792066566311
********************
              precision    recall  f1-score   support

           0       0.80      0.94      0.87     19759
           1       0.93      0.77      0.84     20006

    accuracy                           0.86     39765
   macro avg       0.87      0.86      0.86     39765
weighted avg       0.87      0.86      0.86     39765

********************
85.71% Accurate


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\linear_model\_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is depreca

In [30]:
# decision Tree


DT = DecisionTreeClassifier()
DT.fit(x_train, y_train)
from sklearn.model_selection import cross_val_score

# y_predict = DT.predict(X_test)
print('*'*20)

# prediction
train_pred=DT.predict(x_train)
test_pred= DT.predict(x_test)
print('*'*20)
# accuracy
print('Train accuracy:' , accuracy_score(y_train,train_pred))
print('Test accuracy:' , accuracy_score(y_test,test_pred))

print('*'*20)


print('*'*20)
#  prediction Summary by species
print(classification_report(y_test, test_pred))

print('*'*20)
# Accuracy score
DT_SC = accuracy_score(test_pred,y_test)
print(f"{round(DT_SC*100,2)}% Accurate")

print('*'*20)



c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarn

********************
********************
Train accuracy: 1.0
Test accuracy: 0.9986923173645166
********************
********************
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     19759
           1       1.00      1.00      1.00     20006

    accuracy                           1.00     39765
   macro avg       1.00      1.00      1.00     39765
weighted avg       1.00      1.00      1.00     39765

********************
99.87% Accurate
********************


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarn

In [31]:
# random forest

from sklearn.ensemble import RandomForestClassifier

rfc=RandomForestClassifier(random_state=42)
rfc.fit(x_train,y_train)
print('*'*20)

# prediction
train_prediction= rfc.predict(x_train)
test_prediction= rfc.predict(x_test)
print('*'*20)

# evaluation
from sklearn.metrics import accuracy_score
print('test accuracy:',accuracy_score(y_test,test_prediction))
print('train accuracy:',accuracy_score(y_train,train_prediction))
print('*'*20)

# # cross validation score
# from sklearn.model_selection import cross_val_score
# score=cross_val_score(rfc,X,Y,cv=5)
# print(score.mean())
# print('*'*20)

#  prediction Summary by species
print(classification_report(y_test, test_prediction))
print('*'*20)

# Accuracy score
RF_SC = accuracy_score(test_prediction,y_test)
print(f"{round(RF_SC*100,2)}% Accurate")

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarn

********************


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:767: FutureWarn

********************
test accuracy: 0.9995473406261788
train accuracy: 1.0
********************
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     19759
           1       1.00      1.00      1.00     20006

    accuracy                           1.00     39765
   macro avg       1.00      1.00      1.00     39765
weighted avg       1.00      1.00      1.00     39765

********************
99.95% Accurate


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed 

In [32]:
# Print classification report for each model
print("\nClassification Report for Logistic Regression:\n", classification_report(y_test, test_prediction))
print("\nClassification Report for Decision Tree:\n", classification_report(y_test, test_pred))
print("\nClassification Report for Random Forest:\n", classification_report(y_test, test_prediction))

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed 

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed 


Classification Report for Logistic Regression:
               precision    recall  f1-score   support

           0       1.00      1.00      1.00     19759
           1       1.00      1.00      1.00     20006

    accuracy                           1.00     39765
   macro avg       1.00      1.00      1.00     39765
weighted avg       1.00      1.00      1.00     39765


Classification Report for Decision Tree:
               precision    recall  f1-score   support

           0       1.00      1.00      1.00     19759
           1       1.00      1.00      1.00     20006

    accuracy                           1.00     39765
   macro avg       1.00      1.00      1.00     39765
weighted avg       1.00      1.00      1.00     39765


Classification Report for Random Forest:
               precision    recall  f1-score   support

           0       1.00      1.00      1.00     19759
           1       1.00      1.00      1.00     20006

    accuracy                           1.00    

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\utils\validation.py:614: FutureWarning: is_sparse is deprecated and will be removed 

In [33]:
train_df_pre[train_df_pre['is_fraud'] == 1]

category     amt  gender  is_fraud  age  trans_month  trans_year  \
53437         4  320.85       0         1   22            2        2019   
89510        13   11.62       1         1   30            7        2019   
30049        10   19.79       0         1   42            5        2019   
65692         8  899.80       0         1   60            6        2019   
41810        11  946.78       1         1   33            3        2019   
...         ...     ...     ...       ...  ...          ...         ...   
9200         11  787.72       0         1   47            1        2020   
41671         9    8.75       0         1   84            3        2020   
84432         5   19.38       0         1   41            9        2019   
23151        12  776.21       0         1   17            5        2019   
75464         6  296.61       0         1   43           12        2019   

        lat_dis  long_dis  
53437  0.158999  0.051142  
89510  0.677425  0.963633  
30049  0.466146  0.793970  
65692  0.384728  0.401617  
41810  0.185690  0.625236  
...         ...       ...  
9200   0.113240  0.549939  
41671  0.731217  0.854143  
84432  0.872830  0.098932  
23151  0.173071  0.727429  
75464  0.588684  0.522000  

[588 rows x 9 columns]

In [36]:
train_df_pre[train_df_pre['is_fraud'] == 0]


category     amt  gender  is_fraud  age  trans_month  trans_year  \
21940         2   98.21       1         0   30            9        2019   
83166         4  119.82       1         0   53            6        2019   
72002         8    1.63       1         0   40            6        2019   
46060         4  130.50       1         0   92            4        2019   
97060         4   91.15       0         0   47            5        2019   
...         ...     ...     ...       ...  ...          ...         ...   
93757        10  181.98       0         0   46            7        2019   
18929         7   78.43       0         0   37            7        2019   
84775         8   68.86       0         0   89            7        2019   
99238        12    1.53       1         0   33            5        2020   
45764         0    3.91       1         0   22           11        2019   

        lat_dis  long_dis  
21940  0.180203  0.335115  
83166  0.422473  0.176732  
72002  0.076460  0.164767  
46060  0.749312  0.315109  
97060  0.800461  0.328512  
...         ...       ...  
93757  0.506190  0.283998  
18929  0.601108  0.266172  
84775  0.592024  0.833044  
99238  0.825898  0.177405  
45764  0.802645  0.642900  

[99412 rows x 9 columns]

In [46]:

from sklearn.preprocessing import StandardScaler

# Step 1: Fit the StandardScaler on the training data
# scaler = StandardScaler()
# rfc.predict(scaler.transform([[4,289.76,1,44,8,2020,0.013349,0.854399]]))
rfc.predict(([[4,	119.82	,1	,	53,	6,	2019,	0.422473,	0.176732]]))

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([0], dtype=int64)

In [45]:
rfc.predict(([[12	,776.21	,0,		17,	5,	2019,	0.173071,   	0.727429]]))

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([1], dtype=int64)

In [43]:
rfc.predict(([[8,	852.93,	1	,	18,	6	,2019,	0.715186,	0.878292]]))


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([1], dtype=int64)

In [37]:
rfc.predict(([[2,98.21,	1,30,9,2019,0.180203,0.335115]]))


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([0], dtype=int64)

In [38]:
rfc.predict(([[13	,11.62,	1,		30	,7	,2019,	0.677425,	0.963633]]))############


c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([1], dtype=int64)

In [27]:
# df.to_csv('claimant_clean.csv',index=False)

# from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score

#ML models
from xgboost import XGBClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.neighbors import KNeighborsClassifier

In [28]:
#  XGBoost

XGB = XGBClassifier()
XGB.fit(x_train, y_train)

# prediction
train_prediction= XGB.predict(x_train)
test_prediction= XGB.predict(x_test)
print('*'*20)

# evaluation
from sklearn.metrics import accuracy_score
print('test accuracy:',accuracy_score(y_test,test_prediction))
print('train accuracy:',accuracy_score(y_train,train_prediction))
print('*'*20)

# cross validation score
# from sklearn.model_selection import cross_val_score
# score=cross_val_score(XGB,X,Y,cv=5)
# print(score.mean())
print('*'*20)

print(classification_report(y_test,test_prediction))

print('*'*20)


XGB_HSC = accuracy_score(y_test,test_prediction)
print(f"{round(XGB_HSC*100,2)}% Accurate")

********************
test accuracy: 0.9983652322627701
train accuracy: 0.9996730443967984
********************
0.9984155247118636
********************
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     19769
           1       1.00      1.00      1.00     19992

    accuracy                           1.00     39761
   macro avg       1.00      1.00      1.00     39761
weighted avg       1.00      1.00      1.00     39761

********************
99.84% Accurate


In [29]:
from sklearn.ensemble import AdaBoostClassifier

ada=AdaBoostClassifier(random_state=42)
ada.fit(x_train,y_train)
print('*'*20)

# prediction
train_prediction= ada.predict(x_train)
test_prediction= ada.predict(x_test)
print('*'*20)

# evaluation
from sklearn.metrics import accuracy_score
print('test accuracy:',accuracy_score(y_test,test_prediction))
print('train accuracy:',accuracy_score(y_train,train_prediction))
print('*'*20)

# cross validation score
# from sklearn.model_selection import cross_val_score
# score=cross_val_score(ada,X,Y,cv=5)
# print(score.mean())
print('*'*20)

#  prediction Summary by species
print(classification_report(y_test, test_prediction))
print('*'*20)

# Accuracy score
ada_h = accuracy_score(test_prediction,y_test)
print(f"{round(ada_h*100,2)}% Accurate")

********************
********************
test accuracy: 0.9275169135585121
train accuracy: 0.9283149839980382
********************
********************
              precision    recall  f1-score   support

           0       0.92      0.94      0.93     19769
           1       0.94      0.91      0.93     19992

    accuracy                           0.93     39761
   macro avg       0.93      0.93      0.93     39761
weighted avg       0.93      0.93      0.93     39761

********************
92.75% Accurate


In [30]:
from sklearn.ensemble import GradientBoostingClassifier
# random forest

gbc=GradientBoostingClassifier(random_state=42)
gbc.fit(x_train,y_train)
print('*'*20)

# prediction
train_prediction= gbc.predict(x_train)
test_prediction= gbc.predict(x_test)
print('*'*20)

# evaluation
from sklearn.metrics import accuracy_score
print('test accuracy:',accuracy_score(y_test,test_prediction))
print('train accuracy:',accuracy_score(y_train,train_prediction))
print('*'*20)

# cross validation score
# from sklearn.model_selection import cross_val_score
# score=cross_val_score(gbc,X,Y,cv=5)
# print(score.mean())
print('*'*20)

#  prediction Summary by species
print(classification_report(y_test, test_prediction))
print('*'*20)

# Accuracy score
gbc_h = accuracy_score(test_prediction,y_test)
print(f"{round(gbc_h*100,2)}% Accurate")

********************
********************
test accuracy: 0.9706999320942632
train accuracy: 0.9714542607973944
********************
********************
              precision    recall  f1-score   support

           0       0.98      0.96      0.97     19769
           1       0.97      0.98      0.97     19992

    accuracy                           0.97     39761
   macro avg       0.97      0.97      0.97     39761
weighted avg       0.97      0.97      0.97     39761

********************
97.07% Accurate


In [31]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score

# model
knn_model=KNeighborsClassifier()
knn_model.fit(x_train,y_train)

# prediction

train_prediction= knn_model.predict(x_train)
test_prediction= knn_model.predict(x_test)

# evaluation
print('*'*20)
from sklearn.metrics import accuracy_score
print('Test accuracy:',accuracy_score(y_test,test_prediction))
print('Train accuracy:',accuracy_score(y_train,train_prediction))


print('*'*20)
#  prediction Summary by species
print(classification_report(y_test, test_prediction))


print('*'*20)
# Accuracy score
Knn_SC = accuracy_score(test_prediction,y_test)
print(f"{round(Knn_SC*100,2)}% Accurate")


********************
Test accuracy: 0.9955232514272779
Train accuracy: 0.9971580012952472
********************
              precision    recall  f1-score   support

           0       1.00      0.99      1.00     19769
           1       0.99      1.00      1.00     19992

    accuracy                           1.00     39761
   macro avg       1.00      1.00      1.00     39761
weighted avg       1.00      1.00      1.00     39761

********************
99.55% Accurate


In [32]:
# Undersampling

score = [DT_SC,RF_SC,lr_HSC,Knn_SC,XGB_HSC,ada_h,gbc_h]
Models = pd.DataFrame({
    'Model': ["Decision Tree","Random Forest", "Logistic Regression",'Knn','XGBoost','AdaBoost',"GradientBoostingClassifier"],
    'Score': score})
Models.sort_values(by='Score', ascending=False)

Model     Score
1               Random Forest  0.999547
0               Decision Tree  0.999019
4                     XGBoost  0.998365
3                         Knn  0.995523
6  GradientBoostingClassifier  0.970700
5                    AdaBoost  0.927517
2         Logistic Regression  0.857247

In [33]:
# Oversampling

score = [DT_SC,RF_SC,lr_HSC,Knn_SC,XGB_HSC,ada_h,gbc_h]
Models = pd.DataFrame({
    'Model': ["Decision Tree","Random Forest", "Logistic Regression",'Knn','XGBoost','AdaBoost',"GradientBoostingClassifier"],
    'Score': score})
Models.sort_values(by='Score', ascending=False)

Model     Score
1               Random Forest  0.999547
0               Decision Tree  0.999019
4                     XGBoost  0.998365
3                         Knn  0.995523
6  GradientBoostingClassifier  0.970700
5                    AdaBoost  0.927517
2         Logistic Regression  0.857247

In [39]:
import pickle
#save the model
model = rfc  # Your machine learning model object
file_path = 'rfc_credit1.pkl'  # Path to the file where you want to save the model

with open(file_path, 'wb') as file:
    pickle.dump(model, file)


In [40]:
# load the model
import pickle
file_path = 'rfc_credit1.pkl'  # Path to the saved model file

with open(file_path, 'rb') as file:
    loaded_model = pickle.load(file)

In [42]:
# loaded_model.predict(scaler.transform([[4,316.64,1,66,1,2020,0.7727,0.4476]]))

NameError: name 'scaler' is not defined

In [41]:
loaded_model.predict(([[11	,1053.08,	0,	24,	6,	2020,	0.272626,	0.910465]]))

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([1], dtype=int64)

In [44]:
loaded_model.predict(([[8,	852.93,	1	,	18,	6	,2019,	0.715186,	0.878292]]))

c:\Users\User\Desktop\credit_card_project\creditcardenv\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


array([1], dtype=int64)

In [11]:
train_df_pre[train_df_pre['is_fraud'] == 1]

category      amt  gender  is_fraud  age  trans_month  trans_year  \
70946    grocery_pos   316.92       1         1  NaN          7.0      2019.0   
13678    grocery_pos   331.38       0         1  NaN          NaN         NaN   
6152    shopping_net  1045.55       1         1  NaN          8.0      2020.0   
46266   shopping_net  1097.35       0         1  NaN          2.0      2019.0   
50426    grocery_pos   330.72       1         1  NaN          NaN         NaN   
...              ...      ...     ...       ...  ...          ...         ...   
93830      kids_pets    19.77       0         1  NaN          NaN         NaN   
71812  personal_care    21.33       1         1  NaN          NaN         NaN   
21884       misc_net   888.03       1         1  NaN          NaN         NaN   
39887   shopping_pos   795.17       1         1  NaN          NaN         NaN   
21257    grocery_net    15.05       0         1  NaN          NaN         NaN   

        lat_dis  long_dis  
70946  0.366075  0.410026  
13678  0.761762  0.967497  
6152   0.120236  0.797989  
46266  0.644000  0.387587  
50426  0.955875  0.550017  
...         ...       ...  
93830  0.681102  0.729907  
71812  0.307085  0.147852  
21884  0.918572  0.090858  
39887  0.909859  0.138844  
21257  0.596522  0.441009  

[588 rows x 9 columns]

In [41]:
train_df_pre.describe()

category            amt         gender       is_fraud  \
count  100000.000000  100000.000000  100000.000000  100000.000000   
mean        6.246320      70.073301       0.450510       0.005980   
std         3.917004     148.217515       0.497547       0.077099   
min         0.000000       1.000000       0.000000       0.000000   
25%         3.000000       9.550000       0.000000       0.000000   
50%         6.000000      47.225000       0.000000       0.000000   
75%        10.000000      82.932500       1.000000       0.000000   
max        13.000000   11960.970000       1.000000       1.000000   

                 age   trans_month     trans_year        lat_dis  \
count  100000.000000  100000.00000  100000.000000  100000.000000   
mean       45.534980       6.16547    2019.283790       0.499409   
std        17.371855       3.41611       0.450838       0.288794   
min        13.000000       1.00000    2019.000000       0.000000   
25%        32.000000       3.00000    2019.000000       0.248448   
50%        43.000000       6.00000    2019.000000       0.499847   
75%        57.000000       9.00000    2020.000000       0.749458   
max        95.000000      12.00000    2020.000000       0.999999   

            long_dis  
count  100000.000000  
mean        0.500774  
std         0.288995  
min         0.000000  
25%         0.249526  
50%         0.500809  
75%         0.750764  
max         0.999992

In [45]:
# Assuming train_df_pre is your DataFrame
# For example: train_df_pre = pd.DataFrame(...)

fraudulent_rows = train_df_pre[train_df_pre['is_fraud'] == 1]  # Filtering rows where 'is_fraud' is 1
fraudulent_sorted = fraudulent_rows.sort_values(by='amt', ascending=False)  # Sorting by 'amount'

fraudulent_sorted


category      amt  gender  is_fraud  age  trans_month  trans_year  \
1262544        12  1376.04       0         1   23            6        2020   
514148         12  1371.81       1         1   20            8        2019   
324775         12  1288.29       1         1   18            6        2019   
305250         12  1221.91       1         1   23            5        2019   
427412         11  1205.19       0         1   53            7        2019   
...           ...      ...     ...       ...  ...          ...         ...   
230998          2     7.19       1         1   38            4        2019   
625388         13     6.94       1         1   52            9        2019   
36064           9     6.83       0         1   33            1        2019   
570773          2     6.70       1         1   32            8        2019   
783741          7     5.66       1         1   52           11        2019   

          lat_dis  long_dis  
1262544  0.941008  0.530949  
514148   0.161104  0.819603  
324775   0.531962  0.646116  
305250   0.593522  0.960767  
427412   0.738974  0.065397  
...           ...       ...  
230998   0.379114  0.633589  
625388   0.227810  0.594254  
36064    0.898206  0.473839  
570773   0.574230  0.226610  
783741   0.729764  0.034779  

[598 rows x 9 columns]

In [10]:
import folium

In [9]:
# plotting the lattitude and loggitude
import plotly.express as px
data1 = train_df_pre.copy()
data1.dropna(axis=0,how='any',subset=None,inplace=True)
color_scale = [(0, 'orange'), (1,'red')]
fig = px.scatter_mapbox(data1, lat="lat_dis", lon="long_dis", color_continuous_scale=color_scale,zoom=8, 
                        height=1000,width=1000)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [10]:
import plotly.express as px

# Assuming 'train_df_pre' is a DataFrame containing latitude ('lat_dis') and longitude ('long_dis') columns
# Ensure 'train_df_pre' is properly loaded or replaced with your data source

data1 = train_df_pre.dropna(subset=['lat_dis', 'long_dis']).copy()

color_scale = [(0, 'orange'), (1, 'red')]

fig = px.scatter_mapbox(
    data1,
    lat="lat_dis",
    lon="long_dis",
    color_continuous_scale=color_scale,
    zoom=8,
    height=1000,
    width=1000
)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})

fig.show()


In [22]:
# folium.Map(tiles="cartodb positron")